In [1]:
from qdrant_client import QdrantClient
from qdrant_client.models import Distance, PointStruct, VectorParams
from qdrant_client.models import PointStruct, VectorParams
from qdrant_client import models

/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
baseURL = "http://localhost:6333"
# QDRANT_API_KEY="wRnRbEQU815UgyLrwVVrmwO80wLeodYW4fH1J12_dtg91a_uSwxV_Q"
client = QdrantClient(url=baseURL)



In [8]:
collection_name = "testfile"
client.scroll(
    collection_name=collection_name,
    scroll_filter=models.Filter(
        should=[
            models.FieldCondition(key="document_id", match=models.MatchValue(value="Energy Trading"))
        ]
    ),
)

([Record(id='3d50ccd5-bce3-4f7e-a2e8-069a1916a9cb', payload={'document_id': 'Energy Trading', 'chunk_index': 2, 'filename': 'Energy Trading.pdf', 'chunk-text': 'on to technical skills, I have a collaborative mindset developed through my diverse\nexperiences, including working closely with students and faculty at Technical University of\nDenmark and collaborating with cross-functional teams at Incotec. This background has\nequipped me to work effectively with traders, analysts, and stakeholders to ensure that platform\nimprovements directly impact business outcomes.\n\n\nI am particularly excited about the direct involvement of platform engineers in shaping\nCopenhagen Ener'}, vector=None, shard_key=None, order_value=None),
  Record(id='47d3a00a-f874-422f-b03f-3ed757a1ee2a', payload={'document_id': 'Energy Trading', 'chunk_index': 1, 'filename': 'Energy Trading.pdf', 'chunk-text': ' involving Python-based infrastructure, where I\ndesigned and implemented scalable backend solutions using

In [3]:
collection_name = "example_collection"
client.create_collection(
    collection_name=collection_name,
    vectors_config={
        "text-dense": models.VectorParams(
            size=1536,  # OpenAI Embeddings
            distance=models.Distance.COSINE,
        )
    },
    sparse_vectors_config={
        "text-sparse": models.SparseVectorParams(
            index=models.SparseIndexParams(
                on_disk=False,
            )
        )
    },
)

True

In [4]:
points = [
    PointStruct(
        id=1,
        vector={
            "text-dense": [0.1] * 1536,  # Dense vector
            "text-sparse": models.SparseVector(indices=[6, 7], values=[1.0, 2.0]),
        },
        payload={"filename": f"test"},  # Metadata if needed
    ),
    PointStruct(
        id=2,
        vector={
            "text-dense": [0.101] * 1536,  # Dense vector
            "text-sparse": models.SparseVector(indices=[6, 7], values=[1.0, 2.0]),
        },
        payload={"filename": f"test"},  # Metadata if needed
    ),
    PointStruct(
        id=3,
        vector={
            "text-dense": [0.99] * 1536,  # Dense vector
            "text-sparse": models.SparseVector(indices=[6, 7], values=[1.0, 2.0]),
        },
        payload={"filename": f"point_{3}"},  # Metadata if needed
    ),
]

client.upsert(
    collection_name=collection_name,
    wait=True,
    points=points,
)

UpdateResult(operation_id=0, status=<UpdateStatus.COMPLETED: 'completed'>)

In [25]:
result = client.scroll(
    collection_name="testfile",
    with_payload=True,
    with_vectors=False,
)

In [31]:
type(result), type(result[0]), type(result[1])

(tuple, list, NoneType)

In [118]:
from qdrant_client.models import Record
result2 = ([
  Record(id='13eb202b-1829-4a01-aa7a-c4368cea9a2b', payload={'document_id': 'Kapa', 'chunk_index': 3, 'filename': 'Kapa.ai-Research.pdf', 'chunk-text': 'Some text kapa 1'}, vector=None, shard_key=None, order_value=None),
  Record(id='13eb202b-1829-4a01-aa7a-c4368cea9a2b', payload={'document_id': 'Kapa', 'chunk_index': 1, 'filename': 'Kapa.ai-Research.pdf', 'chunk-text': 'Some text kapa 1'}, vector=None, shard_key=None, order_value=None),
  Record(id='522c1c8a-2d89-4967-9ddc-65ec9016008a', payload={'document_id': 'Kapa', 'chunk_index': 0, 'filename': 'Kapa.ai-Research.pdf', 'chunk-text': 'Some text kapa '}, vector=None, shard_key=None, order_value=None),
  Record(id='522c1c8a-2d89-4967-9ddc-65ec9016008a', payload={'document_id': 'Kapa', 'chunk_index': 2, 'filename': 'Kapa.ai-Research.pdf', 'chunk-text': 'Some text kapa '}, vector=None, shard_key=None, order_value=None),
  Record(id='b0a25b6b-8f1e-4616-8211-4af067bdafac', payload={'document_id': 'Emagine', 'chunk_index': 3, 'filename': 'Emagine.pdf', 'chunk-text': 'Some text emagine '}, vector=None, shard_key=None, order_value=None),
  Record(id='aa9d4554-cbe5-4e62-b1f1-a905869c98c5', payload={'document_id': 'Emagine', 'chunk_index': 0, 'filename': 'Emagine.pdf', 'chunk-text': 'Some text emagine '}, vector=None, shard_key=None, order_value=None),
  Record(id='b0a25b6b-8f1e-4616-8211-4af067bdafac', payload={'document_id': 'Emagine', 'chunk_index': 1, 'filename': 'Emagine.pdf', 'chunk-text': 'Some text emagine '}, vector=None, shard_key=None, order_value=None),
  Record(id='b0a25b6b-8f1e-4616-8211-4af067bdafac', payload={'document_id': 'Emagine', 'chunk_index': 2, 'filename': 'Emagine.pdf', 'chunk-text': 'Some text emagine '}, vector=None, shard_key=None, order_value=None),
  ],
 None)

In [69]:
from typing import Dict, List
from pydantic import BaseModel


class ChunkData(BaseModel):
    chunkText: str


class DocumentData(BaseModel):
    data: List[ChunkData]


class ChunksResponse(BaseModel):
    data: Dict[str, DocumentData]

In [94]:
qdrant_response = result2

for document_index, document_chunks in enumerate(qdrant_response[0], start=1):
    print(
        ChunksResponse(
            data={
                document_chunks.payload["document_id"]: DocumentData(
                    data=[ChunkData(chunkText=document_chunks.payload["chunk-text"])]
                )
            }
        )
    )

data={'Kapa': DocumentData(data=[ChunkData(chunkText='Some text kapa 1')])}
data={'Kapa': DocumentData(data=[ChunkData(chunkText='Some text kapa 2')])}
data={'Emagine': DocumentData(data=[ChunkData(chunkText='Some text emagine 1')])}
data={'Emagine': DocumentData(data=[ChunkData(chunkText='Some text emagine 2')])}


In [ ]:
data = {
    "Kapa": {
        "chunks": [
            "This is a test",
            "This is another test",
        ],
    },
    "Emagine": {
        "chunks": [
            "This is a test",
            "This is another test",
        ],
    },
}

class documentChunks(BaseModel, str)



In [ ]:
transformed_data = {}
qdrant_response = client.scroll(
    collection_name="testfile",
    with_payload=True,
    with_vectors=False,
)


for document_index, document_chunks in enumerate(qdrant_response[0], start=1):
    try:
        transformed_data[document_chunks.payload["document_id"]].append(
            {
                document_chunks.payload["chunk_index"]: document_chunks.payload[
                    "chunk-text"
                ]
            }
        )

    except KeyError:
        transformed_data[document_chunks.payload["document_id"]] = [
            {
                document_chunks.payload["chunk_index"]: document_chunks.payload[
                    "chunk-text"
                ]
            }
        ]


for doc in transformed_data:
    transformed_data[doc] = sorted(
        transformed_data[doc], key=lambda x: list(x.keys())[0]
    )

In [108]:
transformed_data

{'Kapa': [{0: 'Some text kapa 2'}, {1: 'Some text kapa 1'}],
 'Emagine': [{0: 'Some text emagine 1'}, {1: 'Some text emagine 2'}]}

In [138]:
# Define a model for each chunk
class Chunk(BaseModel):
    index: int
    text: str


# Define a model for the entire response
class ChunksResponse(BaseModel):
    data: Dict[str, List[Chunk]]


transformed_data = {}

for document in result2[0]:  # Assuming results[0] contains the Qdrant data
    document_id = document.payload["document_id"]
    chunk_index = document.payload["chunk_index"]
    text = document.payload["chunk-text"]

    if document_id not in transformed_data:
        transformed_data[document_id] = []

    transformed_data[document_id].append({"index": chunk_index, "text": text})

for doc in transformed_data:
    transformed_data[doc] = sorted(transformed_data[doc], key=lambda x: x["index"])
result_transf = ChunksResponse(data=transformed_data)

In [139]:
result_transf

ChunksResponse(data={'Kapa': [Chunk(index=0, text='Some text kapa '), Chunk(index=1, text='Some text kapa 1'), Chunk(index=2, text='Some text kapa '), Chunk(index=3, text='Some text kapa 1')], 'Emagine': [Chunk(index=0, text='Some text emagine '), Chunk(index=1, text='Some text emagine '), Chunk(index=2, text='Some text emagine '), Chunk(index=3, text='Some text emagine ')]})

In [ ]:
ChunksResponse(
    data={
        "Kapa": [
            Chunk(index=3, text="Some text kapa 1"),
            Chunk(index=1, text="Some text kapa 1"),
            Chunk(index=0, text="Some text kapa "),
            Chunk(index=2, text="Some text kapa "),
        ],
        "Emagine": [
            Chunk(index=3, text="Some text emagine "),
            Chunk(index=0, text="Some text emagine "),
            Chunk(index=1, text="Some text emagine "),
            Chunk(index=2, text="Some text emagine "),
        ],
    }
)

ChunksResponse(data={'Kapa': [Chunk(index=3, text='Some text kapa 1'), Chunk(index=1, text='Some text kapa 1'), Chunk(index=0, text='Some text kapa '), Chunk(index=2, text='Some text kapa ')], 'Emagine': [Chunk(index=3, text='Some text emagine '), Chunk(index=0, text='Some text emagine '), Chunk(index=1, text='Some text emagine '), Chunk(index=2, text='Some text emagine ')]})

In [ ]:
data = {
    "Kapa": [
        {
            0: "Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa "
        },
        {
            1: "Some text kapa 1 Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa Some text kapa "
        },
    ],
    "Emagine": [
        {
            0: "Some text emagine 1 Some text emagine 1 Some text emagine 1 Some text emagine 1 Some text emagine 1 Some text emagine 1 "
        },
        {
            1: "Some text emagine 2 Some text emagine 2 Some text emagine 2 Some text emagine 2 Some text emagine 2 Some text emagine 2 Some text emagine 2 "
        },
    ],
}

In [103]:
transformed_data

{'Kapa': [{2: 'Some text kapa 2'}, {3: 'Some text kapa 1'}],
 'Emagine': [{0: 'Some text emagine 1'}, {1: 'Some text emagine 2'}]}

In [ ]:
# transformed_data["Kapa"].sort(key=lambda x: list(x.keys())[0])

In [92]:
sorted(transformed_data["Kapa"], key=lambda x: list(x.keys())[0])

[{0: 'ALEX ABADES GRIMES\nAI Engineer\nDear Finn & Emil,\n\n\nI am writing to express my interest in the Research Engineer position at Kapa.ai. With a Master’s\nin Human-Centered Artificial Intelligence from Denmark’s Technical University and a strong\nbackground in machine learning, retrieval techniques, and AI product development, I am excited\nabout the opportunity to contribute to Kapa’s mission of enhancing technical query resolution\nthrough cutting-edge retrieval and machine learning techniques.\n\n\nIn my previous ro'},
 {1: 'le as Co-Founder at NeoCareU, I led the end-to-end development of Python-\nbased infrastructures, including implementing graph search functionalities using FastAPI, motor,\nand uvicorn. This hands-on experience has provided me with a solid foundation in developing\nrobust and scalable backend solutions. Additionally, I have experience working with retrieval-\naugmented generation (RAG), which aligns closely with Kapa’s focus on improving technical\nquery h

In [93]:
transformed_data

{'Kapa': [{3: 'hank you for considering my application. I look forward to the opportunity to discuss how my\nbackground in AI, deep learning, and search techniques aligns with the goals of Kapa.ai.\n\n\nSincerely,\n\n\nAlex Abades Grimes'},
  {2: ' is further reflected in my research projects. For\ninstance, I’ve developed my own retrieval-augmented generation (RAG) system using natural\nlanguage processing and vector databases. While this system is still evolving and not fully\noptimized for search, it has allowed me to experiment with deploying machine learning models to\ntackle complex data retrieval challenges. This hands-on experience would enable me to\ncontribute effectively to Kapa’s mission of answering more sophisticated technical questions.\n\n\nT'},
  {0: 'ALEX ABADES GRIMES\nAI Engineer\nDear Finn & Emil,\n\n\nI am writing to express my interest in the Research Engineer position at Kapa.ai. With a Master’s\nin Human-Centered Artificial Intelligence from Denmark’s Technical

In [21]:
for document_index, document_chunks in enumerate(result[0], start=1):
  print(document_chunks.id)

1
2
3


In [16]:
type(result[0][0]), result[0][0].id

(qdrant_client.http.models.models.Record, 1)

In [2]:
import random

text_dense_vector = [round(random.random(),2) for _ in range(384)]
print(text_dense_vector)

[0.7, 0.04, 0.3, 0.06, 0.25, 0.88, 0.63, 0.18, 0.42, 0.77, 0.24, 0.96, 0.79, 0.67, 0.72, 0.71, 0.52, 0.16, 0.34, 0.72, 0.13, 0.09, 0.43, 0.74, 0.24, 0.9, 0.58, 0.2, 0.23, 0.43, 0.7, 0.46, 0.14, 0.98, 0.06, 0.39, 0.8, 0.96, 0.2, 0.68, 0.14, 0.65, 0.96, 0.88, 0.21, 0.5, 0.58, 0.76, 0.1, 0.71, 0.62, 0.38, 0.51, 0.35, 0.01, 0.51, 0.39, 0.09, 0.32, 0.31, 0.82, 0.5, 0.74, 0.05, 0.07, 0.25, 0.35, 0.44, 0.98, 0.3, 0.08, 0.08, 0.29, 0.21, 0.0, 0.36, 0.73, 0.82, 0.42, 0.92, 0.11, 0.2, 0.13, 0.32, 0.72, 0.2, 0.7, 0.01, 0.52, 0.86, 0.77, 0.53, 0.14, 0.31, 0.25, 0.23, 0.9, 0.66, 0.44, 0.64, 0.9, 0.26, 0.58, 0.94, 0.5, 0.93, 0.94, 0.57, 0.84, 0.47, 0.68, 0.37, 0.58, 0.35, 0.82, 0.71, 0.32, 0.78, 0.2, 0.27, 0.15, 0.52, 0.32, 0.57, 0.78, 0.42, 0.83, 0.21, 0.29, 0.78, 0.3, 0.97, 0.03, 0.96, 0.49, 0.75, 0.42, 0.9, 0.73, 0.13, 0.85, 0.57, 0.49, 0.85, 0.89, 0.91, 0.3, 0.97, 0.47, 1.0, 0.62, 0.44, 0.54, 0.85, 0.33, 0.25, 0.52, 0.84, 0.68, 0.75, 0.26, 0.01, 0.23, 0.55, 0.65, 0.8, 0.81, 0.54, 0.38, 0.5, 0.51

In [18]:
document_name = "test"
result = client.scroll(
            collection_name=collection_name,
            scroll_filter=models.Filter(
                must=[
                    models.FieldCondition(
                        key="filename", match=models.MatchValue(value=document_name)
                    )
                ]
            ),
        )

In [22]:
[point.id for point in result[0]]

[1, 2]

In [16]:
if result[0]:
  print("somethinf")

In [10]:
client.search(
    collection_name=collection_name,
    query_filter=models.Filter(
        must=[
            models.FieldCondition(
                key="filename", match=models.MatchValue(value=document_name)
            )
        ]
    ),
)


TypeError: QdrantClient.search() missing 1 required positional argument: 'query_vector'

In [17]:
# query_vector_dense = self.dense_embeddings.get_dense_vector(query_text)
# query_vector_sparse = self.dense_embeddings.get_sparse_vector(query_text)

In [19]:
user_query_dense_vector = [0.099] * 1536
user_query_sparse_vector = {6: 2.0, 7: 3.0}


# Dense search
dense_results = client.search(
    collection_name=collection_name,
    query_vector=("text-dense", user_query_dense_vector),
    with_vectors=True,
)

# Sparse search
sparse_results = client.search(
    collection_name=collection_name,
    query_vector=models.NamedSparseVector(
        name="text-sparse",
        vector=models.SparseVector(
            indices=list(user_query_sparse_vector.keys()),
            values=list(user_query_sparse_vector.values()),
        ),
    ),
    with_vectors=True,
)

dense_results, sparse_results

([ScoredPoint(id=3, version=2, score=0.9999997, payload={'name': 'point_3'}, vector={'text-sparse': SparseVector(indices=[6, 7], values=[1.0, 2.0]), 'text-dense': [0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.02

In [8]:
def rrf_fusion_separate_searches(dense_results, sparse_results, k=60):
    combined_scores = {}

    # Rank the dense results
    for rank, point in enumerate(dense_results, start=1):
        if point.id not in combined_scores:
            combined_scores[point.id] = 0
        combined_scores[point.id] += 1 / (k + rank)

    # Rank the sparse results
    for rank, point in enumerate(sparse_results, start=1):
        if point.id not in combined_scores:
            combined_scores[point.id] = 0
        combined_scores[point.id] += 1 / (k + rank)

    # Sort by the combined RRF score
    fused_results = sorted(combined_scores.items(), key=lambda x: x[1], reverse=True)

    return fused_results

In [9]:
# Apply RRF to combine the results
fused_results = rrf_fusion_separate_searches(dense_results, sparse_results)

# Output the fused results with combined RRF scores
for point_id, score in fused_results:
    print(f"Point ID: {point_id}, Combined RRF Score: {score}")

Point ID: 1, Combined RRF Score: 0.03278688524590164


In [62]:
fused_results

[(1, 0.03278688524590164)]

In [7]:
# Hybrid search

client.search_batch(
    collection_name=collection_name,
    requests=[
        models.SearchRequest(
            vector=models.NamedVector(
                name="text-dense",
                vector=query_vector_dense,
            ),
            limit=10,
        ),
        models.SearchRequest(
            vector=models.NamedSparseVector(
                name="text-sparse",
                vector=models.SparseVector(
                    indices=query_indices,
                    values=query_values,
                ),
            ),
            limit=10,
        ),
    ],
)

[[ScoredPoint(id=1, version=0, score=0.9999997, payload=None, vector=None, shard_key=None, order_value=None)],
 [ScoredPoint(id=1, version=0, score=5.0, payload=None, vector=None, shard_key=None, order_value=None)]]

In [14]:
user_query_sparse_vector = {
  6: 1.0,
  7: 2.0
}
user_query_sparse_vector.keys()

dict_keys([6, 7])

In [5]:
# Hybrid search with prefetch and RRF fusion

user_query_dense_vector = [0.099] * 1536
user_query_sparse_vector = {6: 2.0, 7: 3.0}

sparse_dense_rrf_prefetch = models.Prefetch(
    prefetch=[
        models.Prefetch(
            query=user_query_dense_vector,
            using="text-dense",
            limit=25,
        ),
        models.Prefetch(
            query=models.SparseVector(
                indices=list(user_query_sparse_vector.keys()),
                values=list(user_query_sparse_vector.values()),
            ),
            using="text-sparse",
            limit=25,
        ),
    ],
    # RRF fusion
    query=models.FusionQuery(
        fusion=models.Fusion.RRF,
    ),
)

In [9]:
result = client.query_points(
    collection_name=collection_name,
    prefetch=[sparse_dense_rrf_prefetch],
    query=user_query_dense_vector,
    using="text-dense", 
    with_payload=True,
    with_vectors=True,
    limit=10,  
)

In [12]:
result.points

[ScoredPoint(id=3, version=2, score=0.9999997, payload={'name': 'point_3'}, vector={'text-sparse': SparseVector(indices=[6, 7], values=[1.0, 2.0]), 'text-dense': [0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025515523, 0.025

In [13]:
[{"name": point.payload["name"]} for point in result.points]

[{'name': 'point_3'}, {'name': 'point_1'}, {'name': 'point_2'}]

In [15]:
result.points[0].payload['name']

'point_1'

In [ ]:
sparse_dense_rrf_prefetch = models.Prefetch(
    prefetch=[
        models.Prefetch(
            prefetch=[
                # First prefetch retrieves 100 documents with dense vectors
                models.Prefetch(
                    query=dense_vector_low_precision,
                    using="dense-uint8",  # Low precision dense vectors
                    limit=100,
                )
            ],
            # Then, rerank with high-precision dense vectors
            query=user_query_dense_vector,
            using="dense",  # High precision dense vectors
            limit=25,  # Rerank and reduce the number of documents
        ),
        # Another prefetch using sparse vectors
        models.Prefetch(
            query=models.SparseVector(
                indices=list(sparse_vector.keys()),
                values=list(sparse_vector.values()),
            ),
            using="sparse",  # Sparse vector search
            limit=25,
        ),
    ],
    # RRF fusion combines the dense and sparse results
    query=models.FusionQuery(
        fusion=models.Fusion.RRF,  # Reciprocal Rank Fusion
    ),
)

client.query_points(
    collection_name="my-collection",
    prefetch=[sparse_dense_rrf_prefetch],
    # Optional: You can use a late interaction model for final reranking
    query=late_interaction_query_vectors,  # Optional reranking
    using="late-interaction",  # This model reranks the final results
    with_payload=True,
    limit=10,  # Final results
)


In [ ]:
# query_vector_sparse = self.dense_embeddings.get_sparse_vector(query_text)

from torch import cosine_similarity


sparse_results = client.search(
    collection_name=collection_name,
    vector=None,
    sparse_vector={
        "text-sparse": {
            "indices": list(user_query_sparse_vector.keys()),
            "values": list(user_query_sparse_vector.values()),
        }
    },
    limit=100,  # Retrieve more candidates to rerank later
    with_payload=True,
)


# query_vector_dense = self.dense_embeddings.get_dense_vector(query_text)

# Reranking based on dense vectors
reranked_results = sorted(
    sparse_results,
    key=lambda point: cosine_similarity(point.vector["text-dense"], query_vector_dense),
    reverse=True  # Assuming higher cosine similarity is better
)

# Now limit to the top-N results after reranking
top_reranked_results = reranked_results[:10]


In [30]:
points = [
    PointStruct(
        id=str(1),
        vector={"text-dense": [0.0] * 1536},
        sparse_vector={
            "text-sparse": models.SparseVector(indices=[6, 7], values=[1.0, 2.0])
        },
    )
]

client.upsert(
    collection_name=collection_name,
    wait=True,
    points=points,
)

ValidationError: 1 validation error for PointStruct
sparse_vector
  Extra inputs are not permitted [type=extra_forbidden, input_value={'text-sparse': SparseVec... 7], values=[1.0, 2.0])}, input_type=dict]
    For further information visit https://errors.pydantic.dev/2.8/v/extra_forbidden

In [25]:
points = [
    PointStruct(
        id=1,
        vector={"text-dense": [0.1] * 1536},
        payload={"name": f"point_{1}"},
    ),
    PointStruct(
        id=1,
        vector={"text-sparse": models.SparseVector(indices=[6, 7], values=[1.0, 2.0])},
        payload={"name": f"point_{1}"},
    ),
]

In [26]:
client.upsert(
    collection_name=collection_name,
    wait=True,
    points=points,
)

UpdateResult(operation_id=3, status=<UpdateStatus.COMPLETED: 'completed'>)

In [4]:
collections = client.get_collections().collections
collections

[CollectionDescription(name='testfile')]

In [79]:
points = [
    PointStruct(
        id=1,
        vector=[0.1, 0.2, 0.3, 0.4],
        payload={
            "document_id": "Doc_1",
            "chunk_index": 1,
            "filename": "Test_file",
            "text": "This is a test file 2",
        },
    ),
    PointStruct(
        id=2,
        vector=[0.9, 0.9, 0.8, 0.9],
        payload={
            "document_id": "Doc_1",
            "chunk_index": 2,
            "filename": "Test_file",
            "text": "World",
        },
    ),
    PointStruct(
        id=3,
        vector=[0.9, 0.9, 0.8, 0.9],
        payload={
            "document_id": "Doc_1",
            "chunk_index": 2,
            "filename": "Test_file",
            "text": "Hello World",
        },
    ),
    PointStruct(
        id=4,
        vector=[0.9, 0.9, 0.8, 0.9],
        payload={
            "document_id": "Doc_1",
            "chunk_index": 2,
            "filename": "Test_file",
            "text": "Hello I'm Alex",
        },
    ),
]

In [80]:
collection_name = "testfile"
client.upsert(
    collection_name=collection_name,
    wait=True,
    points=points,
)

UpdateResult(operation_id=9, status=<UpdateStatus.COMPLETED: 'completed'>)

In [81]:
client.retrieve(
    collection_name="testfile",
    ids=[1, 2, 3, 4],
)

[Record(id=1, payload={'document_id': 'Doc_1', 'chunk_index': 1, 'filename': 'Test_file', 'text': 'This is a test file 2'}, vector=None, shard_key=None, order_value=None),
 Record(id=2, payload={'document_id': 'Doc_1', 'chunk_index': 2, 'filename': 'Test_file', 'text': 'World'}, vector=None, shard_key=None, order_value=None),
 Record(id=3, payload={'document_id': 'Doc_1', 'chunk_index': 2, 'filename': 'Test_file', 'text': 'Hello World'}, vector=None, shard_key=None, order_value=None),
 Record(id=4, payload={'document_id': 'Doc_1', 'chunk_index': 2, 'filename': 'Test_file', 'text': "Hello I'm Alex"}, vector=None, shard_key=None, order_value=None)]

In [85]:
dense_vector = [0.1, 0.2, 0.3, 0.4]
TEXT = "test"
filter_conditions = models.Filter(
            should=[
                models.FieldCondition(
                    key="text",
                    match=models.MatchText(text="World"),
                )
            ]
        )

search_result = client.query_points(
            collection_name=collection_name,
            query=dense_vector,
            query_filter=filter_conditions,
            search_params=models.SearchParams(hnsw_ef=100, exact=False),
            with_payload=["text"],
            limit=4,
        )

In [86]:
search_result

QueryResponse(points=[ScoredPoint(id=3, version=9, score=0.87, payload={'text': 'Hello World'}, vector=None, shard_key=None, order_value=None), ScoredPoint(id=2, version=9, score=0.87, payload={'text': 'World'}, vector=None, shard_key=None, order_value=None)])

In [68]:
for vec in search_result:
    for scored_point in vec[1]:
        print(scored_point)

In [87]:
import torch
from transformers import AutoTokenizer, AutoModel, AutoModelForMaskedLM
from qdrant_client.http import models as qdrant_models

# Load dense and sparse models
dense_model_name = "sentence-transformers/all-MiniLM-L6-v2"
sparse_model_name = "prithivida/Splade_PP_en_v1"

dense_tokenizer = AutoTokenizer.from_pretrained(dense_model_name)
dense_model = AutoModel.from_pretrained(dense_model_name)

sparse_tokenizer = AutoTokenizer.from_pretrained(sparse_model_name)
sparse_model = AutoModelForMaskedLM.from_pretrained(sparse_model_name)

# Example text chunk
chunk = "This is a sample text for testing dense and sparse vectors."


/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
/home/alexabades/DocuRAG/Api/venv/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more detail